### **Projeto 4** - Resilia + iFood

##### *Grupo 4*: 

*   Aline Santos
*   Gabriela Turquetti
*   Vithor Ribeiro

# **Avanço da pandemia do COVID-19 no Brasil e no mundo**

Neste *notebook* apresentamos a **análise exploratória** realizada com dados mundiais e do Brasil da COVID-19. O objetivo desse projeto é comparar a **gestão do Brasil** com países que possuem **características similares** (e.g. população e produto interno bruto), bem como analisar a **gestão interna** da pandemia em diferentes estados do Brasil.

Para mais informações sobre as **bases de dados** finais, **documentação** desse projeto ou **visualização dos dados** via *Tableau*, acesse nosso [repositório](https://github.com/turquetti/projeto-4-vamoai) no GitHub. 


---

Nossa **análise exploratória** está estruturada da seguinte forma:


1.   **COVID-19 no mundo**
  1. Tratamento das bases de dados
  2. Explorando as bases de dados
  3. Visualização dos dados
2.   **COVID-19 no Brasil**
  1. Tratamento das bases de dados
  2. Explorando as bases de dados
  3. Visualização dos dados
3.   **Referências**


# Bibliotecas

In [3]:
import pandas as pd
import matplotlib.pyplot as plt
import datetime
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from plotly.graph_objs import *
import plotly.express as px
!pip install pycountry
import pycountry
import matplotlib.pyplot as plt
import seaborn as sns
from plotly import tools
import numpy as np

     |████████████████████████████████| 10.1MB 5.5MB/s 
  Created wheel for pycountry: filename=pycountry-20.7.3-py2.py3-none-any.whl size=10746883 sha256=80d1f9018a35a7613a3cb665e7a1887dd7eaef56e1cd3a200f6bf2080df48034
  Stored in directory: /root/.cache/pip/wheels/33/4e/a6/be297e6b83567e537bed9df4a93f8590ec01c1acfbcd405348
Successfully built pycountry


In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


# 1. **COVID-19 no mundo**

Importando as bases de dados com informações mundiais:
*   *COVID Worldwide* - owid-covid-data
*   *GDP Worldwide* - *Gross Domestic Product*
*   *Country* - 


In [ ]:
df_owid = pd.read_csv('/content/drive/MyDrive/Projeto_4/datasets/owid-covid-data.csv')

df_gdp = pd.read_csv('/content/drive/MyDrive/Projeto_4/datasets/gdp.csv').drop(labels='#', axis=1)
df_gdp = df_gdp[df_gdp['GDP (PPP) per capita (2017)'] != 'N.A.']

country = pd.read_csv('/content/drive/MyDrive/Projeto_4/datasets/covid_19_data.csv')

---

### 1.1. Tratando bases de dados

#####   *COVID Worldwide* - owid-covid-data



In [ ]:
df_worldwide = df_owid.fillna(0)
df_worldwide['date'] = pd.to_datetime(df_worldwide['date'])
df_worldwide.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 97125 entries, 0 to 97124
Data columns (total 60 columns):
 #   Column                                 Non-Null Count  Dtype         
---  ------                                 --------------  -----         
 0   iso_code                               97125 non-null  object        
 1   continent                              97125 non-null  object        
 2   location                               97125 non-null  object        
 3   date                                   97125 non-null  datetime64[ns]
 4   total_cases                            97125 non-null  float64       
 5   new_cases                              97125 non-null  float64       
 6   new_cases_smoothed                     97125 non-null  float64       
 7   total_deaths                           97125 non-null  float64       
 8   new_deaths                             97125 non-null  float64       
 9   new_deaths_smoothed                    97125 non-null  float6

In [ ]:
df_worldwide = df_worldwide[['iso_code', 'continent', 'location', 'date', 'total_cases',
                'new_cases', 'total_deaths','total_tests', 'new_deaths', 'population',
                 'gdp_per_capita']]

#####   *GDP Worldwide* - *Gross Domestic Product*



In [ ]:
df_gdp['GDP (PPP) per capita (2017)'] = df_gdp['GDP (PPP) per capita (2017)'].apply(lambda x: float(x.split()[0].replace(',', '')))

In [ ]:
df_gdp['GDP (PPP) per capita (2017)'] = df_gdp['GDP (PPP) per capita (2017)'].astype(int)

In [ ]:
lista_paises = df_gdp['Country'].unique().tolist()

In [ ]:
code_pais = {}

In [ ]:
for pais in lista_paises:
  try:
    pais_data = pycountry.countries.search_fuzzy(pais)
    cp = pais_data[0].alpha_3
    code_pais.update({pais: cp})
  except:
        print('Não foi possível adicionar o code de -> ', pais)
        
        code_pais.update({pais: ' '})

for k, v in code_pais.items():
    df_gdp.loc[(df_gdp['Country'] == k), 'iso_code'] = v

Não foi possível adicionar o code de ->  South Korea
Não foi possível adicionar o code de ->  Czech Republic (Czechia)
Não foi possível adicionar o code de ->  Saint Kitts & Nevis
Não foi possível adicionar o code de ->  St. Vincent & Grenadines
Não foi possível adicionar o code de ->  Laos
Não foi possível adicionar o code de ->  Sao Tome & Principe
Não foi possível adicionar o code de ->  DR Congo


In [ ]:
pib_extract = dict(zip(df_gdp.iso_code, df_gdp['GDP (PPP) per capita (2017)']))

In [ ]:
for k, v in pib_extract.items():
    df_worldwide.loc[(df_worldwide['iso_code'] == k), 'GDP_per_capita_2017'] = v

---

### 1.2. Exploração das bases de dados

#### 1.2.1 - Brasil vs. Mundo

##### Comparação entre os 5 países com população similares ao do Brasil.


In [ ]:
df_population = (
     df_worldwide.loc[(df_worldwide['population']
    .between(200000000,300000000))]
    .sort_values(by='population', ascending = False)
    .drop_duplicates(subset=['location'])
    .groupby(['location','population'])[['location','population','GDP_per_capita_2017']]
).head()

In [ ]:
df_full_population = (
     df_worldwide.loc[(df_worldwide['population']
    .between(200000000,300000000))]
)

Para realizar a filtragem de países que possuem população similar ao do Brasil, delimitamos um intervalo entre 200 milhões e 300 milhões e foi possível observar que países da Asia e África possuem populações próximas à brasileira. Contudo, quando observamos o seu Produto Interno Bruto per capita, ou seja, por população, o Brasil se destaca com o maior PIB, enquanto países como Paquistão e Nigéria possuem PIBs que correspondem a menos de um terço do brasileiro.

In [ ]:
df_population

location   population  GDP_per_capita_2017
40900  Indonesia  273523621.0              12310.0
66737   Pakistan  220892331.0               5539.0
12358     Brazil  212559409.0              15553.0
63651    Nigeria  206139587.0               1019.0

##### Comparação entre os 5 países com PIB similar aos do Brasil.

In [ ]:
df_gdp = (
     df_worldwide.loc[(df_worldwide['GDP_per_capita_2017']
    .between(15000,16000))]
    .sort_values(by='GDP_per_capita_2017', ascending = False)
    .drop_duplicates(subset=['location'])
    .groupby(['location','GDP_per_capita_2017'])[['location','GDP_per_capita_2017','population']]
).head()

In [ ]:
df_full_gdp = (
     df_worldwide.loc[(df_worldwide['GDP_per_capita_2017']
    .between(15000,16000))]
)

De forma a buscar países que possuem PIBs per capita similares ao do Brasil, delimitamos um intervalo entre U$ 15 e 16 mil doláres e foi possível observar que nesse intervalo encontramos países da América do Sul, América do Norte e Europa.
O Brasil é o país que possui maior PIB per capita, bem como maior população. Seguido de países da Europa com populações variando entre 6 e 42 milhões de habitantes. 

In [ ]:
df_gdp

location  GDP_per_capita_2017   population
12711           Brazil              15553.0  212559409.0
77083           Serbia              15432.0    6804596.0
1460           Algeria              15293.0   43851043.0
64979  North Macedonia              15290.0    2083380.0
83843         Suriname              15191.0     586634.0
35595          Grenada              15156.0     112519.0

---

### 1.3. Visualização das bases de dados

##### Panorama da progressão da pandemia no mundo

In [ ]:
df_world_2 = df_worldwide[df_worldwide.location != 'World']
df_world_3 = df_worldwide.sort_values(by=['date'])
df_world_3['date'] = pd.to_datetime(df_world_3['date']).dt.strftime('%Y-%m-%d')

A origem do vírus Sars-CoV-19 é incerta até hoje, mas os primeiros casos registrados foram de um mercado de frutos do mar em Wuran na China. 

Após os primeiros casos registrados, houve um aumento significativo de casos na China e não demorou para que esse vírus se espalhasse por toda a Ásia, principalmente naqueles países que possuiam rotas diretas com a China.

E quando o vírus se instalou na Europa Central, não demorou muito tempo para os primeiros casos de COVID-19 no Brasil serem registrados. 

O Brasil identificou a primeira contaminação pelo COVID-19 no final de fevereiro de 2020 e a primeira declaração de morte pela doença veio em março.

Atualmente, o Brasil é o terceiro país com maior número de casos do mundo, com cerca de 18,622,304 (01/07/2021) e com cerca de 520,095 (01/07/2021)óbitos registrados. 

In [ ]:
fig = px.choropleth(df_world_3, locations="iso_code",
                    color="total_cases",
                    hover_name="location",
                    animation_frame="date",
                    title = "Novos casos de covid diariamente",
                   color_continuous_scale=px.colors.sequential.PuRd)
fig["layout"].pop("updatemenus")
fig.show()

In [ ]:
#arrumar
state_cases=df_worldwide.groupby('location')['total_cases','total_deaths'].max().reset_index()
state_cases["Taxa de Morte (por 100)"] = np.round(100*state_cases["total_deaths"]/state_cases["total_cases"],2)
state_cases.sort_values('total_cases', ascending= False).fillna(0).style.background_gradient(cmap='Reds',subset=["total_cases"])\
                        .background_gradient(cmap='Blues',subset=["total_deaths"])\
                        .background_gradient(cmap='Greys',subset=["Taxa de Morte (por 100)"])\

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



##### Comparação entre os países com população similar ao do Brasil.

*   Número de casos e óbitos por país

O Brasil é o país que possui os maiores índices de casos e óbitos dentre os 4 países. 

Países como a Indonesia, Nigéria e Paquistão possuem índices de casos e óbitos menores, variando entre cerca de 160 mil a 2 milhões de casos e variando entre 2 mil a 55 mil óbitos totais registrados. 

*   Testagem

Contudo, ao observarmos a testagem total entre os países, percebemos que países com as menores taxas, por exemplo, a Nigéria, apesar de possuirem uma população muito próxima ao do Brasil, seu PIB corresponde a 1/15 (quinzeavos) do brasileiro, o que pode justificar o baixo número de casos e óbitos registrados. 

**Foi possível observar também que há correlação entre o PIB per capita e o número de casos e mortes**

O país com maior população, a Indonésia, é o terceiro país da lista que mais testou, com cerca de 12 milhões de testes entre 2020 e 2021. Contudo, apesar do número de testes possivelmente não representar de forma fidedigna o panorama de casos da Indonésia, o país apresenta um número de óbitos muito baixo, correspondente a 55 mil de óbitos registrados.

In [ ]:
df_population

location   population  GDP_per_capita_2017
40900  Indonesia  273523621.0              12310.0
66737   Pakistan  220892331.0               5539.0
12358     Brazil  212559409.0              15553.0
63651    Nigeria  206139587.0               1019.0

In [ ]:
# Numero de casos por país
fig = px.line(
    df_full_population, x='date', y='total_cases',line_group='location', color='location',
    title='Número de casos por país'
)
fig.update_xaxes(title_text='Data')
fig.update_yaxes(title_text='Quantidades')

fig.show()

# Número de mortes por país
fig = px.line(
    df_full_population, x='date', y='total_deaths',line_group='location', color='location',
    title='Número de mortes por país'
)
fig.update_xaxes(title_text='Data')
fig.update_yaxes(title_text='Quantidades')
fig.show()

In [ ]:
df_test = df_full_population.groupby('location').agg({'total_tests':'max'})['total_tests'].reset_index()

# Número de testes por país
fig = px.bar(
    df_test,
    x='location', 
    y='total_tests',
    title='Número de testes por país'
)
fig.update_xaxes(title_text='Data')
fig.update_yaxes(title_text='Quantidades')
fig.show()

##### Comparação entre os 5 países com PIB similar ao do Brasil.

*   **Número de casos e óbitos por PIB**

Novamente, o Brasil é o país que possui os maiores índices de casos e óbitos dentre os países selecionados, contudo ele também é o país mais populoso.


Países como a Servia, Algeria, Macedônia, Suriname e Granada possuem índices de casos e óbitos baixos, variando entre cerca de 161 a 720 mil de casos e variando entre 1 a 7 mil óbitos totais registrados.


*   **Testagem**

Devido aos baixos índices de contaminação no Suriname, Algeria e Granada, não há registro de testagem nesses países. 

Países como a Macedônia foram capazes de testar praticamente metade de sua população, enquanto a Servia foi capaz de testar aproximadamente 70% de toda sua população. 

Essa eficiência de testagem é também refletida nos números de casos e óbitos registrado que são muito inferiores ao panorama brasileiro. 

In [ ]:
df_gdp

location  GDP_per_capita_2017   population
12711           Brazil              15553.0  212559409.0
77083           Serbia              15432.0    6804596.0
1460           Algeria              15293.0   43851043.0
64979  North Macedonia              15290.0    2083380.0
83843         Suriname              15191.0     586634.0
35595          Grenada              15156.0     112519.0

In [ ]:
# Numero de casos por país
fig = px.line(
    df_full_gdp, x='date', y='total_cases',line_group='location', color='location',
    title='Número de casos por país'
)
fig.update_xaxes(title_text='Data')
fig.update_yaxes(title_text='Quantidades')
fig.show()

# Número de mortes por país
fig = px.line(
    df_full_gdp, x='date', y='total_deaths',line_group='location', color='location',
    title='Número de mortes por país'
)
fig.update_xaxes(title_text='Data')
fig.update_yaxes(title_text='Quantidades')
fig.show()

df_test = df_full_gdp.groupby('location').agg({'total_tests':'max'})['total_tests'].reset_index()

# Número de testes por país
fig = px.bar(
    df_test,
    x='location', 
    y='total_tests',
    title='Número de testes por país'
)
fig.update_xaxes(title_text='Data')
fig.update_yaxes(title_text='Quantidades')
fig.show()

# 2. **COVID-19 no Brasil**

Importando as bases de dados com informações brasileiras:
*   *COVID Brasil* - Informações de casos e mortes acumuladas por estado;
*   *Óbitos* - Informações sobre os óbitos acumulados por estado;
*   *PIB* - PIB total por estado do Brasil.

In [4]:
df_brazil = pd.read_csv('/content/drive/MyDrive/Projeto_4/datasets/caso.csv.gz', 
                       compression='gzip')
df_brazil['date'] = pd.to_datetime(df_brazil['date'])
df_brazil = df_brazil.sort_values(by='date', ascending=False)

df_obitos = pd.read_csv('/content/drive/MyDrive/Projeto_4/datasets/obito_cartorio.csv.gz', compression='gzip')

pib_estados = pd.read_csv('/content/drive/MyDrive/Projeto_4/datasets/pib_estados.csv')

---

### 2.1. Tratando bases de dados

#####    *COVID Brasil* - caso.csv


In [5]:
states = {
    'AC': 'Norte',
    'AL': 'Nordeste',
    'AP': 'Norte',
    'AM': 'Norte',
    'BA': 'Nordeste',
    'CE': 'Nordeste',
    'DF': 'Centro-Oeste',
    'ES': 'Sudeste',
    'GO': 'Centro-Oeste',
    'MA': 'Nordeste',
    'MT': 'Centro-Oeste',
    'MS': 'Centro-Oeste',
    'MG': 'Sudeste',
    'PA': 'Norte',
    'PB': 'Nordeste',
    'PR': 'Sul',
    'PE': 'Nordeste',
    'PI': 'Nordeste',
    'RJ': 'Sudeste',
    'RN': 'Nordeste',
    'RS': 'Sul',
    'RO': 'Norte',
    'RR': 'Norte',
    'SC': 'Sul',
    'SP': 'Sudeste',
    'SE': 'Nordeste',
    'TO': 'Centro-Oeste'
}

In [6]:
for k,v in states.items():
  df_brazil.loc[( 
                df_brazil['state'] == k
                
  ),'region'] = v

In [7]:
todos_estados = (
    df_brazil.groupby(['state']).agg({'confirmed':'max', 'deaths':'max', 
                                           'estimated_population':'max'})
).reset_index().sort_values('confirmed', ascending= False)

for k,v in states.items():
  todos_estados.loc[( 
                todos_estados['state'] == k
                
  ),'region'] = v

In [8]:
todos_estados_obitos = todos_estados.sort_values('deaths', ascending=False)

#####   *PIB* - pib_estados.csv

In [9]:
pib_estados.sort_values(by="2018", ascending=False)

Unidade da Federação          2018
26            São Paulo  2.210562e+09
25       Rio de Janeiro  7.588590e+08
24         Minas Gerais  6.148758e+08
23    Rio Grande do Sul  4.572940e+08
22               Paraná  4.400294e+08
21       Santa Catarina  2.982271e+08
20                Bahia  2.862395e+08
19     Distrito Federal  2.548172e+08
18                Goiás  1.956817e+08
17           Pernambuco  1.863520e+08
16                 Pará  1.613496e+08
15                Ceará  1.559038e+08
14          Mato Grosso  1.374429e+08
13       Espírito Santo  1.370201e+08
12   Mato Grosso do Sul  1.069691e+08
11             Amazonas  1.001092e+08
10             Maranhão  9.817950e+07
9   Rio Grande do Norte  6.696956e+07
8               Paraíba  6.437360e+07
7               Alagoas  5.441305e+07
6                 Piauí  5.037842e+07
5              Rondônia  4.491398e+07
4               Sergipe  4.201798e+07
3             Tocantins  3.566618e+07
2                 Amapá  1.679521e+07
1                  Acre  1.533112e+07
0               Roraima  1.336999e+07

In [10]:
state_names = {
    'AC': 'Acre',
    'AL': 'Alagoas',
    'AP': 'Amapá',
    'AM': 'Amazonas',
    'BA': 'Bahia',
    'CE': 'Ceará',
    'DF': 'Distrito Federal',
    'ES': 'Espírito Santo',
    'GO': 'Goiás',
    'MA': 'Maranhão',
    'MT': 'Mato Grosso',
    'MS': 'Mato Grosso do Sul',
    'MG': 'Minas Gerais',
    'PA': 'Pará',
    'PB': 'Paraíba',
    'PR': 'Paraná',
    'PE': 'Pernambuco',
    'PI': 'Piauí',
    'RJ': 'Rio de Janeiro',
    'RN': 'Rio Grande do Norte',
    'RS': 'Rio Grande do Sul',
    'RO': 'Rondônia',
    'RR': 'Roraima',
    'SC': 'Santa Catarina',
    'SP': 'São Paulo',
    'SE': 'Sergipe',
    'TO': 'Tocantins'
}

In [11]:
for k,v in state_names.items():
  pib_estados.loc[( 
                pib_estados['Unidade da Federação'] == v
                
  ),'iso_code'] = k

In [12]:
# Manipulando df_caso_brazil
df_estimated_population = (
    df_brazil.loc[(df_brazil['place_type'] == 'state')].drop_duplicates(subset='state')
    .groupby('state')[['estimated_population', 'state']].head()
).reset_index()
df_estimated_population = df_estimated_population[['state','estimated_population']]
df_estimated_population = df_estimated_population.sort_values(by='state', ascending=True).reset_index()

# Manipulando pib_estados
pib_estados = pib_estados.sort_values(by='iso_code', ascending=True).reset_index()

In [13]:
pib_estados['estimated_population'] = df_estimated_population['estimated_population']

In [14]:
#Calculando pib per capita de cada estado
pib_estados = pib_estados[['Unidade da Federação','2018','iso_code','estimated_population']]
pib_estados['pib_per_capita'] = pib_estados['2018']/pib_estados['estimated_population']
pib_estados = pib_estados.sort_values('pib_per_capita', ascending=False)
pib_estados

Unidade da Federação          2018  ... estimated_population  pib_per_capita
6      Distrito Federal  2.548172e+08  ...            3055149.0       83.405819
25            São Paulo  2.210562e+09  ...           46289333.0       47.755321
18       Rio de Janeiro  7.588590e+08  ...           17366189.0       43.697500
23       Santa Catarina  2.982271e+08  ...            7252502.0       41.120580
22    Rio Grande do Sul  4.572940e+08  ...           11422973.0       40.032832
12          Mato Grosso  1.374429e+08  ...            3526220.0       38.977390
17               Paraná  4.400294e+08  ...           11516840.0       38.207477
11   Mato Grosso do Sul  1.069691e+08  ...            2809394.0       38.075522
7        Espírito Santo  1.370201e+08  ...            4064052.0       33.715133
10         Minas Gerais  6.148758e+08  ...           21292666.0       28.877352
8                 Goiás  1.956817e+08  ...            7113540.0       27.508347
20             Rondônia  4.491398e+07  ...            1796460.0       25.001379
2              Amazonas  1.001092e+08  ...            4207714.0       23.791834
26            Tocantins  3.566618e+07  ...            1590248.0       22.428063
21              Roraima  1.336999e+07  ...             631181.0       21.182494
3                 Amapá  1.679521e+07  ...             861773.0       19.489131
15           Pernambuco  1.863520e+08  ...            9616621.0       19.378114
4                 Bahia  2.862395e+08  ...           14930634.0       19.171292
19  Rio Grande do Norte  6.696956e+07  ...            3534165.0       18.949189
13                 Pará  1.613496e+08  ...            8690745.0       18.565681
24              Sergipe  4.201798e+07  ...            2318822.0       18.120399
0                  Acre  1.533112e+07  ...             894470.0       17.139896
5                 Ceará  1.559038e+08  ...            9187103.0       16.969857
1               Alagoas  5.441305e+07  ...            3351543.0       16.235223
14              Paraíba  6.437360e+07  ...            4039277.0       15.936910
16                Piauí  5.037842e+07  ...            3281480.0       15.352347
9              Maranhão  9.817950e+07  ...            7114598.0       13.799725

[27 rows x 5 columns]



#####   Óbitos - obitos.csv



In [ ]:
df_obitos = df_obitos.fillna(0)
df_obitos['date'] = pd.to_datetime(df_obitos['date'])
df_obitos.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9882 entries, 0 to 9881
Data columns (total 34 columns):
 #   Column                               Non-Null Count  Dtype         
---  ------                               --------------  -----         
 0   date                                 9882 non-null   datetime64[ns]
 1   state                                9882 non-null   object        
 2   epidemiological_week_2019            9882 non-null   int64         
 3   epidemiological_week_2020            9882 non-null   int64         
 4   deaths_indeterminate_2019            9882 non-null   int64         
 5   deaths_respiratory_failure_2019      9882 non-null   int64         
 6   deaths_others_2019                   9882 non-null   int64         
 7   deaths_pneumonia_2019                9882 non-null   int64         
 8   deaths_septicemia_2019               9882 non-null   int64         
 9   deaths_sars_2019                     9882 non-null   int64         
 10  deaths_covid

---

### 2.2. Exploração das bases de dados

##### Panorama do Brasil

No Brasil, os estados que apresentam os maiores índices de contaminação e óbitos são aqueles das regiões Sudeste (São Paulo, Rio de Janeiro e Minas Gerais) e Sul (Paraná e Rio Grande do Sul). 

O número de casos da região Sudeste, especialmente São Paulo, é coerente visto que essa região foi o epicentro da pandemia do COVID-19 em fevereiro de 2020.

As regiões que possuem menores índices de contaminação e óbitos são Centro-Oeste, Nordeste e Norte. 

In [ ]:
todos_estados

state  confirmed  deaths  estimated_population        region
25    SP    3696093  126050            46289333.0       Sudeste
10    MG    1786654   45888            21292666.0       Sudeste
17    PR    1269017   30445            11516840.0           Sul
22    RS    1209799   31117            11422973.0           Sul
4     BA    1119127   23739            14930634.0      Nordeste
23    SC    1046141   16706             7252502.0           Sul
18    RJ     951360   55181            17366189.0       Sudeste
5     CE     880418   22442             9187103.0      Nordeste
8     GO     671228   18988             7113540.0  Centro-Oeste
13    PA     549610   15420             8690745.0         Norte
15    PE     546537   17551             9616621.0      Nordeste
7     ES     514907   11417             4064052.0       Sudeste
12    MT     448308   11926             3526220.0  Centro-Oeste
6     DF     428352    9193             3055149.0  Centro-Oeste
2     AM     400781   13271             4207714.0         Norte
14    PB     391811    8538             4039277.0      Nordeste
19    RN     336217    6722             3534165.0      Nordeste
11    MS     333050    8089             2809394.0  Centro-Oeste
9     MA     315104    8962             7114598.0      Nordeste
16    PI     295008    6554             3281480.0      Nordeste
24    SE     262447    5652             2318822.0      Nordeste
20    RO     246818    6113             1796460.0         Norte
1     AL     214509    5281             3351543.0      Nordeste
26    TO     196509    3179             1590248.0  Centro-Oeste
3     AP     116708    1824              861773.0         Norte
21    RR     111720    1731              631181.0         Norte
0     AC      85463    1736              894470.0         Norte

#####    Comparação PIBs do Brasil

#####    Comparação entre causas de óbitos dos anos de 2019 e 2020

In [ ]:
# insuficiencia respiratória
df_obitos.max()[['deaths_respiratory_failure_2019','deaths_respiratory_failure_2020']]

# pneumonia
df_obitos.max()[['deaths_pneumonia_2019','deaths_pneumonia_2020']]

# septicemia
df_obitos.max()[['deaths_septicemia_2019','deaths_septicemia_2020']]

# sars
df_obitos.max()[['deaths_sars_2019','deaths_sars_2020']]

#mortes indeterminadas
df_obitos.max()[['deaths_indeterminate_2019','deaths_indeterminate_2020']]

deaths_indeterminate_2019    1855
deaths_indeterminate_2020    1943
dtype: object

---

### 2.3. Visualização das bases de dados

##### Panorama do Brasil

Os estados que apresentam os maiores índices são aqueles das regiões Sudeste e Sul. 

O número de casos da região Sudeste, especialmente São Paulo, é coerente visto que essa região foi o epicentro da pandemia do COVID-19 em fevereiro de 2020.

As regiões que possuem menores índices de contaminação e óbitos são Centro-Oeste, Nordeste e Norte.

In [ ]:
#Visualização de dados confirmados por estado
fig = px.bar(todos_estados, y='state', x='confirmed', text='confirmed', color='state', orientation='h')
fig.update_traces(texttemplate='%{text:.2s}', textposition='outside')
fig.show()

In [ ]:
#Visualização de óbitos confirmados por estado
fig = px.bar(todos_estados_obitos, y='state', x='deaths', text='deaths', color='state', orientation='h')
fig.update_traces(texttemplate='%{text:.2s}', textposition='outside')
fig.show()

##### Panorama do Brasil por região

In [ ]:
# Mortes por região do brasil
fig = px.bar(todos_estados, x="region", color="region",
             y='deaths',
             title="Mortes em cada região",
             barmode='relative',
             height=600
            )
fig.show()

In [ ]:
#Visualização de dados confirmados por regiao
trace1 = Bar(
    x=todos_estados.loc[(todos_estados['region'] == 'Sudeste')]['state'],
    y=todos_estados.loc[(todos_estados['region'] == 'Sudeste')]['confirmed'],
    name='Sudeste'
)
trace2 = Bar(
    x=todos_estados.loc[(todos_estados['region'] == 'Nordeste')]['state'],
    y=todos_estados.loc[(todos_estados['region'] == 'Nordeste')]['confirmed'],
    name='Nordeste'
)
trace3 = Bar(
    x=todos_estados.loc[(todos_estados['region'] == 'Centro-Oeste')]['state'],
    y=todos_estados.loc[(todos_estados['region'] == 'Centro-Oeste')]['confirmed'],
    name='Centro-Oeste'
)
trace4 = Bar(
    x=todos_estados.loc[(todos_estados['region'] == 'Norte')]['state'],
    y=todos_estados.loc[(todos_estados['region'] == 'Norte')]['confirmed'],
    name='Norte'
)
trace5 = Bar(
    x=todos_estados.loc[(todos_estados['region'] == 'Sul')]['state'],
    y=todos_estados.loc[(todos_estados['region'] == 'Sul')]['confirmed'],
    name='Sul'
)
fig = tools.make_subplots(rows=1, cols=1, shared_xaxes=True)

fig.append_trace(trace1, 1, 1)
fig.append_trace(trace2,1,1)
fig.append_trace(trace3,1,1)
fig.append_trace(trace4,1,1)
fig.append_trace(trace5,1,1)

fig['layout'].update(height=800, width=1000)
fig.show()

/usr/local/lib/python3.7/dist-packages/plotly/tools.py:465: DeprecationWarning:

plotly.tools.make_subplots is deprecated, please use plotly.subplots.make_subplots instead



In [ ]:
fig = make_subplots(rows=1, cols=2, specs=[[{"type": "xy"}, {"type": "xy"}]],
)
fig.add_trace(
    go.Scatter(name='Casos',x=df_sudeste['date'], y=df_sudeste['confirmed']),
    row=1, col=1
)

fig.add_trace(
    go.Scatter(name='Mortes',x=df_sudeste['date'], y=df_sudeste['deaths']),
    row=1, col=2
)
fig.update_layout(title_text="Casos confirmados / Mortes confirmadas")
fig.show()

# **Referências**

*COVID-19 no Mundo*
*   `owid-covid-data.csv` - [owid](https://github.com/owid/covid-19-data/)
*   `gdp.csv` - [World Meter](https://www.worldometers.info/gdp/gdp-per-capita/)

*COVID-19 no Brasil*
*   `case.csv` - [Brasil.io](https://brasil.io/dataset/covid19/caso/)
*   `obito_cartorio.csv` - [Brasil.io](https://brasil.io/dataset/covid19/obito_cartorio/)
*   `pib_estados.csv` - [IBGE](https://sidra.ibge.gov.br/tabela/5938) (Informações extraídas referentes ao ano de 2018)

